# Model accruracy comparison

## Setup

In [1]:
import tensorflow as tf

#> Hide GPU from visible devices

tf.config.set_visible_devices([], 'GPU')

2023-02-10 19:48:17.634599: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 AVX512F AVX512_VNNI FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-02-10 19:48:17.851607: I tensorflow/core/util/port.cc:104] oneDNN custom operations are on. You may see slightly different numerical results due to floating-point round-off errors from different computation orders. To turn them off, set the environment variable `TF_ENABLE_ONEDNN_OPTS=0`.
2023-02-10 19:48:17.857419: W tensorflow/compiler/xla/stream_executor/platform/default/dso_loader.cc:64] Could not load dynamic library 'libcudart.so.11.0'; dlerror: libcudart.so.11.0: cannot open shared object file: No such file or directory
2023-02-10 19:48:17.857449: I tensorflow/compiler/xla/stream_executor/cuda/cudart_stub.cc:29] Ignore 

In [2]:
#> Check you are indeed running on a CPU

tf.debugging.set_log_device_placement(True)

#> Create some tensors and perform an operation

a = tf.constant([[1.0, 2.0, 3.0], [4.0, 5.0, 6.0]])
b = tf.constant([[1.0, 2.0], [3.0, 4.0], [5.0, 6.0]])
c = tf.matmul(a, b)

print(c)

Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op _MklMatMul in device /job:localhost/replica:0/task:0/device:CPU:0
tf.Tensor(
[[22. 28.]
 [49. 64.]], shape=(2, 2), dtype=float32)


2023-02-10 19:48:20.249163: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 AVX512F AVX512_VNNI FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.
2023-02-10 19:48:20.277700: I tensorflow/core/common_runtime/placer.cc:114] input: (_Arg): /job:localhost/replica:0/task:0/device:CPU:0
2023-02-10 19:48:20.277742: I tensorflow/core/common_runtime/placer.cc:114] _EagerConst: (_EagerConst): /job:localhost/replica:0/task:0/device:CPU:0
2023-02-10 19:48:20.277751: I tensorflow/core/common_runtime/placer.cc:114] output_RetVal: (_Retval): /job:localhost/replica:0/task:0/device:CPU:0
2023-02-10 19:48:20.294600: I tensorflow/core/common_runtime/placer.cc:114] a: (_Arg): /job:localhost/replica:0/task:0/device:CPU:0
2023-02-10 19:48:20.294643: I tensorflow/core/common_runtime/placer.cc:114

In [3]:
pathdataset = "imgs2train"

# Transfer learning: EfficientNetB0

In [4]:
# baseline model for the dogs vs cats dataset
import sys
import tensorflow as tf
from matplotlib import pyplot
from tensorflow.keras.utils import to_categorical
from keras.models import Sequential
from keras.layers import Conv2D
from keras.layers import MaxPooling2D
from keras.layers import Dense
from keras.layers import Flatten
from keras.layers import Input
from keras.layers import Dropout
from tensorflow.keras.optimizers import SGD
from keras.preprocessing.image import ImageDataGenerator
import numpy as np
from keras.models import Model
from sklearn.metrics import confusion_matrix
import os
from tensorflow.keras.optimizers import SGD

In [5]:
import efficientnet.keras as efn
from tensorflow.keras import layers
from tensorflow.keras.optimizers import legacy as L

## Model performance function: EfficientNetB0

In [6]:
#> paramenter:
#> architecture = ["VGG16", "Inception"]
#> learning_rate = [0.001, 0.005, 0.0001] 
#> epochs = [50, 100] 

#> Model setup

def define_model(architecture = "EfficientNetB0", loss = 'binary_crossentropy', learning_rate = 0.001, epochs = 50, rep = 1):  
    model = efn.EfficientNetB0(input_shape = (200, 200, 3), include_top = False, weights = 'imagenet')
    # mark loaded layers as not trainable
    for layer in model.layers:
        layer.trainable = False
    x = model.output
    x = Flatten()(x)
    x = Dense(1024, activation="relu")(x)
    x = Dropout(0.5)(x)

    x = model.output
    x = Flatten()(x)
    x = Dense(1024, activation="relu")(x)
    x = Dropout(0.5)(x)

    # Add a final sigmoid layer with 1 node for classification output
    predictions = Dense(1, activation="sigmoid")(x)
    model = Model(model.input, predictions)
    return model

In [7]:
#> Model accuracy

def run_test_harness(architecture = "EfficientNetB0", loss = 'binary_crossentropy', learning_rate = 0.001, epochs = 50, rep = 1):
    for i in range(rep):
        model = define_model(architecture, loss, learning_rate, epochs)
        # create data generator
        datagen = ImageDataGenerator(rescale=1.0/255.0)
        # prepare iterator
        train_it = datagen.flow_from_directory(pathdataset+'/train/',
            class_mode='binary', batch_size=64, target_size=(200, 200))
        test_it = datagen.flow_from_directory(pathdataset+'/val/',
            class_mode='binary', batch_size=64, target_size=(200, 200))

        optimizer = L.RMSprop(learning_rate = learning_rate, decay=1e-6)
        model.compile(optimizer = optimizer, loss = loss, metrics=['accuracy'])
        eff_history = model.fit(train_it, validation_data = test_it,  epochs = epochs)
        # evaluate model
        _, acc = model.evaluate(test_it, steps=len(test_it))
        print('> %.3f' % (acc * 100.0))
        #> learning curves
        #summarize_diagnostics(history)
        #> save model
        modelName = architecture+"-"+loss+"-"+str(learning_rate)+"-"+str(epochs)+"-"+"{}"+"-"+str(round(acc*100, 4))+".h5"       
        model.save(modelName.format(i+1))

## Model performace: EfficientNetB0

In [ ]:
#> learning_rate & epochs = 25

run_test_harness(architecture = "EfficientNetB0", loss = 'binary_crossentropy', learning_rate = 0.001, epochs = 25, rep = 3)
run_test_harness(architecture = "EfficientNetB0", loss = 'binary_crossentropy', learning_rate = 0.005, epochs = 25, rep = 3)
run_test_harness(architecture = "EfficientNetB0", loss = 'binary_crossentropy', learning_rate = 0.0001, epochs = 25, rep = 3)

Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op StatelessRandomGetKeyCounter in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op StatelessTruncatedNormalV2 in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op Mul in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op AddV2 in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op VarHandleOp in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op AssignVariableOp in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op _Eag

Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op StatelessRandomGetKeyCounter in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op StatelessTruncatedNormalV2 in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op Mul in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op AddV2 in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op VarHandleOp in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op AssignVariableOp in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op Fill in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op VarHandleOp in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op AssignVaria

2023-02-10 19:49:19.239878: I tensorflow/core/common_runtime/placer.cc:114] input: (_Arg): /job:localhost/replica:0/task:0/device:CPU:0
2023-02-10 19:49:19.239924: I tensorflow/core/common_runtime/placer.cc:114] _EagerConst: (_EagerConst): /job:localhost/replica:0/task:0/device:CPU:0
2023-02-10 19:49:19.239935: I tensorflow/core/common_runtime/placer.cc:114] output_RetVal: (_Retval): /job:localhost/replica:0/task:0/device:CPU:0
2023-02-10 19:49:19.250591: I tensorflow/core/common_runtime/placer.cc:114] seed: (_Arg): /job:localhost/replica:0/task:0/device:CPU:0
2023-02-10 19:49:19.250630: I tensorflow/core/common_runtime/placer.cc:114] StatelessRandomGetKeyCounter: (StatelessRandomGetKeyCounter): /job:localhost/replica:0/task:0/device:CPU:0
2023-02-10 19:49:19.250639: I tensorflow/core/common_runtime/placer.cc:114] key_RetVal: (_Retval): /job:localhost/replica:0/task:0/device:CPU:0
2023-02-10 19:49:19.250647: I tensorflow/core/common_runtime/placer.cc:114] counter_RetVal: (_Retval): /jo

Executing op AssignVariableOp in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op Fill in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op VarHandleOp in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op AssignVariableOp in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op Fill in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op VarHandleOp in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op AssignVariableOp in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op Fill in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op VarHandleOp in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op AssignVariableOp in device /job:l

Executing op VarHandleOp in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op AssignVariableOp in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op Fill in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op VarHandleOp in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op AssignVariableOp in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op _EagerConst in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op Fill in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op VarHandleOp in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op AssignVariableOp in device /job:localhost/replica:0/task:0/device:CPU:0


...

1/4 [======>.......................] - ETA: 9s - loss: 1.7231 - accuracy: 0.7969Executing op ReadVariableOp in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op Identity in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op __inference_train_function_48731 in device /job:localhost/replica:0/task:0/device:CPU:0
2/4 [==============>...............] - ETA: 5s - loss: 3.7018 - accuracy: 0.7812Executing op ReadVariableOp in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op Identity in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op __inference_train_function_48731 in device /job:localhost/replica:0/task:0/device:CPU:0
3/4 [=====================>........] - ETA: 2s - loss: 3.3420 - accuracy: 0.7816Executing op ReadVariableOp in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op Identity in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op __inference_train_function_48731 in device /job:localhost/replica

2023-02-10 20:05:31.510758: I tensorflow/core/common_runtime/placer.cc:114] args_0: (_Arg): /job:localhost/replica:0/task:0/device:CPU:0
2023-02-10 20:05:31.510813: I tensorflow/core/common_runtime/placer.cc:114] GeneratorDataset: (GeneratorDataset): /job:localhost/replica:0/task:0/device:CPU:0
2023-02-10 20:05:31.510830: I tensorflow/core/common_runtime/placer.cc:114] NoOp: (NoOp): /job:localhost/replica:0/task:0/device:CPU:0
2023-02-10 20:05:31.510840: I tensorflow/core/common_runtime/placer.cc:114] Identity: (Identity): /job:localhost/replica:0/task:0/device:CPU:0
2023-02-10 20:05:31.510852: I tensorflow/core/common_runtime/placer.cc:114] FakeSink0: (Identity): /job:localhost/replica:0/task:0/device:CPU:0
2023-02-10 20:05:31.510862: I tensorflow/core/common_runtime/placer.cc:114] identity_RetVal: (_Retval): /job:localhost/replica:0/task:0/device:CPU:0
2023-02-10 20:05:31.523339: I tensorflow/core/common_runtime/placer.cc:114] args_0: (_Arg): /job:localhost/replica:0/task:0/device:CP

Executing op ReadVariableOp in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op Identity in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op __inference_test_function_50588 in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op ReadVariableOp in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op ReadVariableOp in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op DivNoNan in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op Identity in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op ReadVariableOp in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op ReadVariableOp in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op DivNoNan in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op Identity in device /job:localhost/replica:0/task:0/device:CPU:0
4/4 [==============================] - 16s 4s/step - loss: 3.4483 - accuracy: 0.7647 - val_loss: 3.0

2023-02-10 20:05:35.282625: I tensorflow/core/common_runtime/placer.cc:114] args_0: (_Arg): /job:localhost/replica:0/task:0/device:CPU:0
2023-02-10 20:05:35.282683: I tensorflow/core/common_runtime/placer.cc:114] GeneratorDataset: (GeneratorDataset): /job:localhost/replica:0/task:0/device:CPU:0
2023-02-10 20:05:35.282699: I tensorflow/core/common_runtime/placer.cc:114] NoOp: (NoOp): /job:localhost/replica:0/task:0/device:CPU:0
2023-02-10 20:05:35.282713: I tensorflow/core/common_runtime/placer.cc:114] Identity: (Identity): /job:localhost/replica:0/task:0/device:CPU:0
2023-02-10 20:05:35.282725: I tensorflow/core/common_runtime/placer.cc:114] FakeSink0: (Identity): /job:localhost/replica:0/task:0/device:CPU:0
2023-02-10 20:05:35.282737: I tensorflow/core/common_runtime/placer.cc:114] identity_RetVal: (_Retval): /job:localhost/replica:0/task:0/device:CPU:0
2023-02-10 20:05:35.333456: I tensorflow/core/common_runtime/placer.cc:114] args_0: (_Arg): /job:localhost/replica:0/task:0/device:CP

1/4 [======>.......................] - ETA: 13s - loss: 1.9316 - accuracy: 0.8594Executing op ReadVariableOp in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op Identity in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op __inference_train_function_48731 in device /job:localhost/replica:0/task:0/device:CPU:0
2/4 [==============>...............] - ETA: 2s - loss: 1.1409 - accuracy: 0.9091 Executing op ReadVariableOp in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op Identity in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op __inference_train_function_48731 in device /job:localhost/replica:0/task:0/device:CPU:0
3/4 [=====================>........] - ETA: 2s - loss: 0.7847 - accuracy: 0.9368Executing op ReadVariableOp in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op Identity in device /job:localhost/replica:0/task:0/device:CPU:0
Executing op __inference_train_function_48731 in device /job:localhost/repli

In [ ]:
#> learning_rate & epochs = 50

run_test_harness(architecture = "EfficientNetB0", loss = 'binary_crossentropy', learning_rate = 0.001, epochs = 50, rep = 3)
run_test_harness(architecture = "EfficientNetB0", loss = 'binary_crossentropy', learning_rate = 0.005, epochs = 50, rep = 3)
run_test_harness(architecture = "EfficientNetB0", loss = 'binary_crossentropy', learning_rate = 0.0001, epochs = 50, rep = 3)

In [ ]:
#> learning_rate & epochs = 75

run_test_harness(architecture = "EfficientNetB0", loss = 'binary_crossentropy', learning_rate = 0.001, epochs = 75, rep = 3)
run_test_harness(architecture = "EfficientNetB0", loss = 'binary_crossentropy', learning_rate = 0.005, epochs = 75, rep = 3)
run_test_harness(architecture = "EfficientNetB0", loss = 'binary_crossentropy', learning_rate = 0.0001, epochs = 75, rep = 3)

In [ ]:
#> learning_rate & epochs = 100

run_test_harness(architecture = "EfficientNetB0", loss = 'binary_crossentropy', learning_rate = 0.001, epochs = 100, rep = 3)
run_test_harness(architecture = "EfficientNetB0", loss = 'binary_crossentropy', learning_rate = 0.005, epochs = 100, rep = 3)
run_test_harness(architecture = "EfficientNetB0", loss = 'binary_crossentropy', learning_rate = 0.0001, epochs = 100, rep = 3)

# Transfer learning: ResNet50

In [ ]:
#> Baseline model for the dogs vs cats dataset

import sys
import tensorflow as tf
from matplotlib import pyplot
from tensorflow.keras.utils import to_categorical
from keras.models import Sequential
from keras.layers import Conv2D
from keras.layers import MaxPooling2D
from keras.layers import Dense
from keras.layers import Flatten
from keras.layers import Input
from tensorflow.keras.optimizers import SGD
from keras.preprocessing.image import ImageDataGenerator
import numpy as np
from keras.models import Model
from sklearn.metrics import confusion_matrix
import os
from tensorflow.keras.optimizers import SGD

In [ ]:
from tensorflow.keras.applications import ResNet50
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense, Flatten, GlobalAveragePooling2D
from tensorflow.keras.optimizers import SGD

## Model performance function: ResNet50

In [ ]:
#> paramenter:
#> architecture = ["VGG16", "Inception"]
#> learning_rate = [0.001, 0.005, 0.0001] 
#> epochs = [50, 100] 

#> Model setup

def define_model(architecture = "ResNet50", loss = 'binary_crossentropy', learning_rate = 0.001, epochs = 50, rep = 1):
    # load model
    model = ResNet50(input_shape=(200, 200,3), include_top=False, weights="imagenet")
    # mark loaded layers as not trainable
    for layer in model.layers:
        layer.trainable = False
    
    model = Sequential()
    model.add(ResNet50(include_top=False, weights='imagenet', pooling='max'))
    model.add(Dense(1, activation='sigmoid'))

    optimizer = SGD(learning_rate = learning_rate, momentum=0.9)
    model.compile(optimizer = optimizer, loss = loss, metrics = ['accuracy'])
    return model

In [ ]:
#> Model accuracy

def run_test_harness(architecture = "ResNet50", loss = 'binary_crossentropy', learning_rate = 0.001, epochs = 50, rep = 1):
    for i in range(rep):
        #> define model
        model = define_model(architecture, loss, learning_rate, epochs)
        # create data generator
        datagen = ImageDataGenerator(rescale=1.0/255.0)
        # prepare iterator
        train_it = datagen.flow_from_directory(pathdataset+'/train/',
            class_mode='binary', batch_size=64, target_size=(200, 200))
        test_it = datagen.flow_from_directory(pathdataset+'/val/',
            class_mode='binary', batch_size=64, target_size=(200, 200))

        resnet_history = model.fit(train_it, validation_data = test_it, 
                                        steps_per_epoch = epochs, epochs = epochs)

        # evaluate model
        _, acc = model.evaluate(test_it, steps=len(test_it))
        print('> %.3f' % (acc * 100.0))
        #> learning curves
        #summarize_diagnostics(history)
        #> save model
        modelName = architecture+"-"+loss+"-"+str(learning_rate)+"-"+str(epochs)+"-"+"{}"+"-"+str(round(acc*100, 4))+".h5"       
        model.save(modelName.format(i+1))

## Model performace: ResNet50

In [ ]:
#> learning_rate & epochs = 25

run_test_harness(architecture = "ResNet50", loss = 'binary_crossentropy', learning_rate = 0.001, epochs = 25, rep = 3)
run_test_harness(architecture = "ResNet50", loss = 'binary_crossentropy', learning_rate = 0.005, epochs = 25, rep = 3)
run_test_harness(architecture = "ResNet50", loss = 'binary_crossentropy', learning_rate = 0.0001, epochs = 25, rep = 3)

In [ ]:
#> learning_rate & epochs = 50

run_test_harness(architecture = "ResNet50", loss = 'binary_crossentropy', learning_rate = 0.001, epochs = 50, rep = 3)
run_test_harness(architecture = "ResNet50", loss = 'binary_crossentropy', learning_rate = 0.005, epochs = 50, rep = 3)
run_test_harness(architecture = "ResNet50", loss = 'binary_crossentropy', learning_rate = 0.0001, epochs = 50, rep = 3)

In [ ]:
#> learning_rate & epochs = 75

run_test_harness(architecture = "ResNet50", loss = 'binary_crossentropy', learning_rate = 0.001, epochs = 75, rep = 3)
run_test_harness(architecture = "ResNet50", loss = 'binary_crossentropy', learning_rate = 0.005, epochs = 75, rep = 3)
run_test_harness(architecture = "ResNet50", loss = 'binary_crossentropy', learning_rate = 0.0001, epochs = 75, rep = 3)

In [ ]:
#> learning_rate & epochs = 100

run_test_harness(architecture = "ResNet50", loss = 'binary_crossentropy', learning_rate = 0.001, epochs = 100, rep = 3)
run_test_harness(architecture = "ResNet50", loss = 'binary_crossentropy', learning_rate = 0.005, epochs = 100, rep = 3)
run_test_harness(architecture = "ResNet50", loss = 'binary_crossentropy', learning_rate = 0.0001, epochs = 100, rep = 3)

# Transfer learning: VGG16

In [ ]:
#> Baseline model for the dogs vs cats dataset

import sys
from matplotlib import pyplot
from tensorflow.keras.utils import to_categorical
from keras.models import Sequential
from keras.layers import Conv2D
from keras.layers import MaxPooling2D
from keras.layers import Dense
from keras.layers import Flatten
from keras.layers import Input
from tensorflow.keras.optimizers import SGD
from keras.preprocessing.image import ImageDataGenerator
import numpy as np
from sklearn.metrics import confusion_matrix

In [ ]:
from keras.models import Model
from keras.applications.vgg16 import VGG16

## Model performance function: VGG16

In [ ]:
#> paramenter:
#> architecture = ["VGG16", "Inception"]
#> learning_rate = [0.001, 0.005, 0.0001] 
#> epochs = [50, 100] 

#> Model setup

def define_model(architecture = "VGG16", loss = 'binary_crossentropy', learning_rate = 0.001, epochs = 50, rep = 1):
	# load model
	model = VGG16(include_top=False, input_shape=(200, 200, 3))
	# mark loaded layers as not trainable
	for layer in model.layers:
		layer.trainable = False
	# add new classifier layers
	flat1 = Flatten()(model.layers[-1].output)
	class1 = Dense(128, activation='relu', kernel_initializer='he_uniform')(flat1)
	output = Dense(1, activation='sigmoid')(class1)
	# define new model
	model = Model(inputs=model.inputs, outputs=output)
	# compile model
	opt = SGD(learning_rate = learning_rate, momentum=0.9) # model param
	model.compile(optimizer=opt, loss = loss, metrics=['accuracy'])
	return model

#> Model accuracy

def run_test_harness(architecture = "VGG16", loss = 'binary_crossentropy', learning_rate = 0.001, epochs = 50, rep = 1):
    for i in range(rep):
        #> define model
        model = define_model(architecture, loss, learning_rate, epochs)
        #> create data generator
        datagen = ImageDataGenerator(rescale=1.0/255.0)
        #> prepare iterator
        train_it = datagen.flow_from_directory(pathdataset+'/train/',
                                               class_mode='binary', batch_size=64, target_size=(200, 200))
        test_it = datagen.flow_from_directory(pathdataset+'/val/',
                                              class_mode='binary', batch_size=64, target_size=(200, 200))
        #> fit model
        history = model.fit(train_it, steps_per_epoch=len(train_it),
                            validation_data=test_it, validation_steps=len(test_it), epochs = epochs, verbose = 0)
        #> evaluate model
        _, acc = model.evaluate(test_it, steps=len(test_it), verbose = 0)
        print('> %.3f' % (acc * 100.0))
        #> learning curves
        #summarize_diagnostics(history)
        #> save model
        modelName = architecture+"-"+loss+"-"+str(learning_rate)+"-"+str(epochs)+"-"+"{}"+"-"+str(round(acc*100, 4))+".h5"       
        model.save(modelName.format(i+1))

## Model performace: VGG16 architecture

#> paramenter:
#> learning_rate = [0.001, 0.005, 0.0001] 
#> epochs = [50, 100] 

In [ ]:
#> learning_rate & epochs = 25

run_test_harness(architecture = "VGG16", loss = 'binary_crossentropy', learning_rate = 0.001, epochs = 25, rep = 3)
run_test_harness(architecture = "VGG16", loss = 'binary_crossentropy', learning_rate = 0.005, epochs = 25, rep = 3)
run_test_harness(architecture = "VGG16", loss = 'binary_crossentropy', learning_rate = 0.0001, epochs = 25, rep = 3)

In [ ]:
#> learning_rate & epochs = 50

run_test_harness(architecture = "VGG16", loss = 'binary_crossentropy', learning_rate = 0.001, epochs = 50, rep = 3)
run_test_harness(architecture = "VGG16", loss = 'binary_crossentropy', learning_rate = 0.005, epochs = 50, rep = 3)
run_test_harness(architecture = "VGG16", loss = 'binary_crossentropy', learning_rate = 0.0001, epochs = 50, rep = 3)

In [ ]:
#> learning_rate & epochs = 75

run_test_harness(architecture = "VGG16", loss = 'binary_crossentropy', learning_rate = 0.001, epochs = 75, rep = 3)
run_test_harness(architecture = "VGG16", loss = 'binary_crossentropy', learning_rate = 0.005, epochs = 75, rep = 3)
run_test_harness(architecture = "VGG16", loss = 'binary_crossentropy', learning_rate = 0.0001, epochs = 75, rep = 3)

In [ ]:
#> learning_rate & epochs = 100

run_test_harness(architecture = "VGG16", loss = 'binary_crossentropy', learning_rate = 0.001, epochs = 100, rep = 3)
run_test_harness(architecture = "VGG16", loss = 'binary_crossentropy', learning_rate = 0.005, epochs = 100, rep = 3)
run_test_harness(architecture = "VGG16", loss = 'binary_crossentropy', learning_rate = 0.0001, epochs = 100, rep = 3)

# Transfer learning: InceptionV3

In [ ]:
# baseline model for the dogs vs cats dataset
import sys
import tensorflow as tf
from matplotlib import pyplot
from tensorflow.keras.utils import to_categorical
from keras.models import Sequential
from keras.layers import Conv2D
from keras.layers import MaxPooling2D
from keras.layers import Dense
from keras.layers import Flatten
from keras.layers import Input
from tensorflow.keras.optimizers import SGD
from keras.preprocessing.image import ImageDataGenerator
import numpy as np
from sklearn.metrics import confusion_matrix
import os

In [ ]:
from tensorflow.keras.applications.inception_v3 import InceptionV3
from tensorflow.keras.optimizers import RMSprop
from tensorflow.keras import layers

## Model performance function: InceptionV3

In [ ]:
#> paramenter:
#> architecture = ["VGG16", "Inception"]
#> learning_rate = [0.001, 0.005, 0.0001] 
#> epochs = [50, 100] 

#> Model setup

def define_model(architecture = "InceptionV3", loss = 'binary_crossentropy', learning_rate = 0.001, epochs = 50, rep = 1):
    #> load model
    model = InceptionV3(input_shape = (200, 200, 3), include_top = False, weights = 'imagenet')
    #> mark loaded layers as not trainable
    for layer in model.layers:
        layer.trainable = False
        from tensorflow.keras.optimizers import RMSprop
        x = layers.Flatten()(model.output)
        x = layers.Dense(128, activation = 'relu')(x)
        x = layers.Dropout(0.2)(x)

    #> Add a final sigmoid layer with 1 node for classification output
    x = layers.Dense(1, activation = 'sigmoid')(x)
    
    model = tf.keras.models.Model(model.input, x)
    model.compile(optimizer = RMSprop(learning_rate = learning_rate), loss = loss, metrics = ['acc'])
    return model

#> Model accuracy

def run_test_harness(architecture = "InceptionV3", loss = 'binary_crossentropy', learning_rate = 0.001, epochs = 50, rep = 1):
    for i in range(rep):
        #> define model
        model = define_model(architecture, loss, learning_rate, epochs)    
        #> create data generator
        datagen = ImageDataGenerator(rescale=1.0/255.0)
        #> prepare iterator
        train_it = datagen.flow_from_directory(pathdataset+'/train/',
                                               class_mode='binary', batch_size = 64, target_size = (200, 200))
        test_it = datagen.flow_from_directory(pathdataset+'/val/',
                                              class_mode='binary', batch_size = 64, target_size = (200, 200))
        #> fit model
        history = model.fit(train_it, steps_per_epoch = len(train_it),
                            validation_data = test_it, validation_steps=len(test_it), epochs = epochs)
        # evaluate model
        _, acc = model.evaluate_generator(test_it, steps=len(test_it))
        print('> %.3f' % (acc * 100.0))
        # learning curves
        #summarize_diagnostics(history)
        #save model
        modelName = architecture+"-"+loss+"-"+str(learning_rate)+"-"+str(epochs)+"-"+"{}"+"-"+str(round(acc*100, 4))+".h5"
        model.save(modelName.format(i+1))

## Model performace: InceptionV3 architecture

In [ ]:
#> learning_rate & epochs = 25

run_test_harness(architecture = "InceptionV3", loss = 'binary_crossentropy', learning_rate = 0.001, epochs = 25, rep = 3)
run_test_harness(architecture = "InceptionV3", loss = 'binary_crossentropy', learning_rate = 0.005, epochs = 25, rep = 3)
run_test_harness(architecture = "InceptionV3", loss = 'binary_crossentropy', learning_rate = 0.0001, epochs = 25, rep = 3)

In [ ]:
#> learning_rate & epochs = 50

run_test_harness(architecture = "InceptionV3", loss = 'binary_crossentropy', learning_rate = 0.001, epochs = 50, rep = 3)
run_test_harness(architecture = "InceptionV3", loss = 'binary_crossentropy', learning_rate = 0.005, epochs = 50, rep = 3)
run_test_harness(architecture = "InceptionV3", loss = 'binary_crossentropy', learning_rate = 0.0001, epochs = 50, rep = 3)

In [ ]:
#> learning_rate & epochs = 75

run_test_harness(architecture = "InceptionV3", loss = 'binary_crossentropy', learning_rate = 0.001, epochs = 75, rep = 3)
run_test_harness(architecture = "InceptionV3", loss = 'binary_crossentropy', learning_rate = 0.005, epochs = 75, rep = 3)
run_test_harness(architecture = "InceptionV3", loss = 'binary_crossentropy', learning_rate = 0.0001, epochs = 75, rep = 3)

In [ ]:
#> learning_rate & epochs = 100

run_test_harness(architecture = "InceptionV3", loss = 'binary_crossentropy', learning_rate = 0.001, epochs = 100, rep = 3)
run_test_harness(architecture = "InceptionV3", loss = 'binary_crossentropy', learning_rate = 0.005, epochs = 100, rep = 3)
run_test_harness(architecture = "InceptionV3", loss = 'binary_crossentropy', learning_rate = 0.0001, epochs = 100, rep = 3)

# Best model performance

In [ ]:
import os
import pandas as pd
from keras.models import load_model
from tensorflow.keras.utils import load_img
from tensorflow.keras.utils import img_to_array

In [ ]:
#> folders to train
imagepath = "imgs2train" 
imagepath = "imageJ" 
#> best model selection
bstmodel = 'VGG16-binary_crossentropy-0.001-75-3-91.1392.h5'
model = load_model(bstmodel)

In [ ]:
# load and prepare the image
def load_image(filename):
	# load the image
	img = load_img(filename, target_size=(200, 200))
	# convert to array
	img = img_to_array(img)
	# reshape into a single sample with 3 channels
	img = img.reshape(1, 200, 200, 3)
	# center pixel data
	img = img.astype('float32')
	img = img - [123.68, 116.779, 103.939]
	return img

In [ ]:
root_dir = imagepath

file_paths = []

for root, dirs, files in os.walk(root_dir):
    for file in files:
        if file.endswith(".jpg") or file.endswith(".png"):
            file_path = os.path.join(root, file)
            file_paths.append(file_path)
            
print(file_paths)

In [ ]:
#> glomerulate = 1
#> amaranth = 0

pandasdata = pd.DataFrame({'imgname': [],'metric_classification_result': [],'class': []})

for i in range(len(file_paths)):
    image= file_paths[i]
    print(image)
    img = load_image(image)
    result = model.predict(img)
    classif=0
    if result[0]<=0.1: 
        print("Image is classified as amaranth!")
        classif="amaranth"
    elif result[0]>=0.9:
        print("Image is classified as glomerulate!")
        classif="glomerulate"
    else:
        print("Image cannot be clearly classified!")
        classif=""
    
    pandasdata=pandasdata.append({'imgname': file_paths[i],'metric_classification_result': result[0],'class': classif},
                                    ignore_index=True) 


pandasdata.to_csv(imagepath + "_" + bstmodel + '.csv', sep = ',')